In [1]:
import re
import tensorflow as tf
# from collections import Counter
import gensim
import numpy as np
# count = Counter()

In [2]:
import tensorflow as tf
print("Num GPUs Available: ", len(tf.config.list_physical_devices('GPU')))

Num GPUs Available:  1


In [60]:
import lzma

X_train = lzma.open("train/in.tsv.xz", mode='rt', encoding='utf-8').readlines()
Y_train = open("train/expected.tsv", "r").readlines()
X_dev0 = lzma.open("dev-0/in.tsv.xz", mode='rt', encoding='utf-8').readlines()
y_expected_dev0 = open("dev-0/expected.tsv", "r").readlines()
X_test = lzma.open("test-A/in.tsv.xz", mode='rt', encoding='utf-8').readlines()

In [4]:
X_train

['have you had an medical issues recently?\t1335187994\n',
 "It's supposedly aluminum, barium, and strontium being used in large-scale weather modification.\t1346187161\n",
 "Nobel prizes don't make you rich.\t1337160218\n",
 'I came for the article, I stayed for the doctor.\t1277674344\n',
 "you resorted to insults AND got owned directly afterwards. that's a double-whammy\t1348538535\n",
 'Spirituality?  Oh hey no thanks, you can keep the crazy for yourself.\t1310932399\n',
 'I took a "ghost tour" last year and was handed one of these along with others on the tour.\\n\\nThere was some excitement in one area when people picked up readings.\\n\\nI noticed and pointed out some undergrounded utilities there.  Excitement dimmed.\\n\\nThough I *did* enjoy the tour.  The guide was interesting and knew all the local legends, places where people died or were killed, and a bunch of other historical goodies.  It was worth going.\t1326401425\n',
 "Oh, I've heard the name... I've heard that he has

In [5]:
# X_train = [x[:100] for x in X_train ]

In [6]:
Y_train = [float(i.replace('\n', '')) for i in Y_train]
Y_train

[1.0,
 0.0,
 0.0,
 0.0,
 0.0,
 1.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 1.0,
 1.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 1.0,
 1.0,
 0.0,
 0.0,
 0.0,
 0.0,
 1.0,
 0.0,
 0.0,
 1.0,
 0.0,
 1.0,
 0.0,
 0.0,
 1.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 1.0,
 0.0,
 0.0,
 0.0,
 0.0,
 1.0,
 1.0,
 0.0,
 1.0,
 0.0,
 1.0,
 0.0,
 1.0,
 1.0,
 0.0,
 1.0,
 0.0,
 0.0,
 0.0,
 1.0,
 0.0,
 0.0,
 1.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 1.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 1.0,
 0.0,
 1.0,
 1.0,
 0.0,
 0.0,
 1.0,
 1.0,
 0.0,
 0.0,
 0.0,
 0.0,
 1.0,
 0.0,
 1.0,
 1.0,
 0.0,
 0.0,
 0.0,
 0.0,
 1.0,
 0.0,
 0.0,
 0.0,
 1.0,
 1.0,
 0.0,
 1.0,
 1.0,
 0.0,
 0.0,
 1.0,
 0.0,
 0.0,
 1.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 1.0,
 0.0,
 1.0,
 0.0,
 0.0,
 0.0,
 1.0,
 0.0,
 0.0,
 1.0,
 0.0,
 0.0,
 0.0,
 0.0,
 1.0,
 0.0,
 1.0,
 0.0,
 0.0,
 1.0,
 1.0,
 0.0,
 1.0,
 1.0,
 0.0,
 0.0,
 0.0,
 1.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 1.0,
 0.0,
 0.0,
 0.0,
 1.0,
 1.0,
 1.0,
 0.0,
 0.0

In [7]:
X_train = [i.split('\t')[0] for i in X_train]
X_train

['have you had an medical issues recently?',
 "It's supposedly aluminum, barium, and strontium being used in large-scale weather modification.",
 "Nobel prizes don't make you rich.",
 'I came for the article, I stayed for the doctor.',
 "you resorted to insults AND got owned directly afterwards. that's a double-whammy",
 'Spirituality?  Oh hey no thanks, you can keep the crazy for yourself.',
 'I took a "ghost tour" last year and was handed one of these along with others on the tour.\\n\\nThere was some excitement in one area when people picked up readings.\\n\\nI noticed and pointed out some undergrounded utilities there.  Excitement dimmed.\\n\\nThough I *did* enjoy the tour.  The guide was interesting and knew all the local legends, places where people died or were killed, and a bunch of other historical goodies.  It was worth going.',
 "Oh, I've heard the name... I've heard that he has been banned from reddit multiple times too.\\n\\nI must have skipped over that part.",
 "Yeah, it

In [8]:
# import nltk
# from nltk.corpus import stopwords
# nltk.download('stopwords')
# # from nltk.tokenize import word_tokenize

# # tokens_without_sw = [word for word in text_tokens if not word in stopwords.words()]


In [9]:
# def preprocess(line):
#     txt = line
# #     txt = re.sub(
# #         "(£|§|!|@|#|\$|%|\^|&|\*|\(|\)|_|-|\+|=|\{|\[|\}|\]|:|;|\"|'|\|\\|\<|,|\>|\.|\?|/|~|`|\|–|–|)",
# #         "",
# #         txt,
# #     )
#     txt = txt.lower()
# #     txt = re.sub("[0-9]", "", txt)
# #     txt = re.sub("[ \t]+", " ", txt)
# #     txt = re.sub(" +$", "", txt)
# #     txt = re.sub("ą", "a", txt)
# #     txt = re.sub("ć", "c", txt)
# #     txt = re.sub("ę", "e", txt)
# #     txt = re.sub("ł", "l", txt)
# #     txt = re.sub("ń", "n", txt)
# #     txt = re.sub("ó", "o", txt)
# #     txt = re.sub("ś", "s", txt)
# #     txt = re.sub("ź", "z", txt)
# #     txt = re.sub("ż", "z", txt)
#     words = txt.split()
#     words = [word for word in words if not word in stopwords.words()]
#     words = [w[:8] if len(w) > 8 else w for w in words]
#     out = []
# #     for word in words:
# #           out.append(word)
#     for stem in words:
#         count[stem] += 1
#     text = " ".join(out)
# #     print(text)
#     return text


In [10]:
# text = ' '.join([word for word in text.split() if word not in cachedStopWords])


In [11]:
# temp = []
# stopword =  stopwords.words()
# for i in X_train:
#     words = [word for word in i.split() if word not in stopword]
#     temp.append(' '.join([w[:8] if len(w) > 8 else w for w in words]))
# temp

In [12]:
from keras.preprocessing.text import Tokenizer
num_words = 20000
tokenizer = Tokenizer(num_words=num_words)
tokenizer.fit_on_texts(X_train)

In [69]:
X_train = (tokenizer.texts_to_sequences(X_train))
X_dev0 = (tokenizer.texts_to_sequences(X_dev0))
X_test = (tokenizer.texts_to_sequences(X_test))

In [70]:
X_test

[[9844, 8, 100, 38, 43, 243, 7, 13, 9, 3, 8280],
 [1, 213, 9, 7, 10, 68, 27, 672, 10, 156, 3296, 19, 310, 132, 15, 2123],
 [95,
  1021,
  2,
  51,
  1163,
  11247,
  1,
  169,
  7,
  1013,
  1266,
  11,
  1,
  1249,
  400,
  450,
  139,
  7146,
  39,
  513,
  9,
  149,
  126,
  63,
  2095,
  48,
  6410,
  13,
  311,
  9,
  149],
 [45,
  62,
  26,
  13,
  9,
  28,
  12,
  14,
  317,
  15,
  19,
  1,
  415,
  2206,
  2,
  1,
  462,
  1658,
  83,
  37,
  1035,
  30,
  3,
  1435,
  25,
  39,
  373,
  118,
  24,
  1800,
  30,
  1,
  210,
  656,
  3169,
  11,
  13,
  891,
  15,
  3,
  98,
  1180,
  729,
  785],
 [8, 1152, 28, 114, 173, 338, 8, 27, 45, 52, 5, 658, 99, 1, 107, 94],
 [114, 671, 13, 4, 1, 441, 1407, 56, 2254, 404, 9, 123, 2769, 897, 5, 1139],
 [8,
  45,
  62,
  7,
  31,
  19,
  31,
  97,
  165,
  70,
  40,
  4647,
  271,
  12,
  78,
  1,
  46,
  554,
  716,
  22,
  1,
  17023,
  1204,
  23,
  7,
  85,
  127,
  8,
  502,
  40,
  6090,
  9,
  2955],
 [322,
  6,
  106,
  294,
  91,

In [71]:
from keras.preprocessing.sequence import pad_sequences
max_len = 50
X_train = pad_sequences(
    X_train, maxlen=max_len, padding="post", truncating="post"
)
X_dev0 = pad_sequences(
    X_dev0, maxlen=max_len, padding="post", truncating="post"
)
X_test = pad_sequences(
   X_test, maxlen=max_len, padding="post", truncating="post"
)

In [72]:
X_test

array([[9844,    8,  100, ...,    0,    0,    0],
       [   1,  213,    9, ...,    0,    0,    0],
       [  95, 1021,    2, ...,    0,    0,    0],
       ...,
       [ 391,  629, 2369, ...,   20, 2549,   97],
       [1074,    7,   24, ...,    0,    0,    0],
       [  24,  161, 1205, ...,    0,    0,    0]])

In [17]:
import keras
early_stopping = keras.callbacks.EarlyStopping(
    monitor="val_loss", patience=20, restore_best_weights=True, verbose=0
)

# checkpoint_callback = keras.callbacks.ModelCheckpoint(
#         filepath='.', monitor='val_loss', verbose=0, save_weights_only=True,
#         save_freq='epoch', mode='auto', save_best_only=True)

reduce_lr_on_plateau = keras.callbacks.ReduceLROnPlateau(
    monitor="acc", factor=0.1, patience=5, verbose=0
)

callbacks_list = [early_stopping, reduce_lr_on_plateau]

In [18]:
from tensorflow.keras.layers import Embedding

def gensim_to_keras_embedding(model, train_embeddings=False):
    """Get a Keras 'Embedding' layer with weights set from Word2Vec model's learned word embeddings.

    Parameters
    ----------
    train_embeddings : bool
        If False, the returned weights are frozen and stopped from being updated.
        If True, the weights can / will be further updated in Keras.

    Returns
    -------
    `keras.layers.Embedding`
        Embedding layer, to be used as input to deeper network layers.

    """
    keyed_vectors = model.wv  # structure holding the result of training
    weights = keyed_vectors.vectors  # vectors themselves, a 2D numpy array    
    index_to_key = keyed_vectors.index_to_key  # which row in `weights` corresponds to which word?

    layer = Embedding(
    input_dim,
    output_dim,
    )
    return layer

In [19]:
# from gensim import downloader
# glove_vectors = gensim.downloader.load('glove-twitter-25')

In [20]:
# glove_vectors

In [46]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import (
    Flatten,
    Dense,
    Embedding,
    Dropout,
)

model = Sequential()
# model.add(Embedding(
#         input_dim=10000,
#         output_dim=512,
#         input_length=50
# ))
model.add(Embedding(
        input_dim=10000,
        output_dim=4,
        input_length=50
))
model.add(Flatten())
model.add(
    Dense(
        units=256,
        activation="relu"))
model.add(Dropout(0.1))
# model.add(
#     Dense(
#         units=512,
#         activation="relu"))
# model.add(Dropout(0.1))
model.add(
    Dense(
        units=128,
        activation="relu"))  
model.add(Dense(1, activation="sigmoid"))
model.compile(optimizer="adam", loss="binary_crossentropy", metrics=["acc"])
model.summary()


Model: "sequential_6"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding_6 (Embedding)     (None, 50, 4)             40000     
                                                                 
 flatten_6 (Flatten)         (None, 200)               0         
                                                                 
 dense_19 (Dense)            (None, 256)               51456     
                                                                 
 dropout_7 (Dropout)         (None, 256)               0         
                                                                 
 dense_20 (Dense)            (None, 128)               32896     
                                                                 
 dense_21 (Dense)            (None, 1)                 129       
                                                                 
Total params: 124,481
Trainable params: 124,481
Non-tr

In [42]:
# tuner = kt.Hyperband(
#     build_model,
#     "val_loss",
#     20,
#     factor=2,
#     hyperband_iterations=1,
# )

In [23]:
len(Y_train)

289579

In [24]:
from collections import Counter


print(Counter(Y_train).keys()) # equals to list(set(words))
print(Counter(Y_train).values()) # counts the elements' frequency

dict_keys([1.0, 0.0])
dict_values([104076, 185503])


In [25]:
from sklearn.utils import class_weight
class_weights = class_weight.compute_class_weight('balanced',
                                                 np.unique(Y_train),
                                                 Y_train)
class_weights

C:\Users\Karol Idaszak\AppData\Local\Programs\Python\Python37\lib\site-packages\sklearn\utils\validation.py:72: FutureWarning: Pass classes=[0. 1.], y=[1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 1.0, 0.0, 1.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 1.0, 0.0, 1.0, 0.0, 1.0, 0.0, 1.0, 1.0, 0.0, 1.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 1.0, 1.0, 0.0, 0.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 1.0, 1.0, 0.0, 1.0, 1.0, 0.0, 0.0, 1.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 1.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 1.0, 0.0, 0.0, 1.0, 1.0, 0.0, 1.0, 1.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 1.0, 1.0, 1.0, 0.0, 0.0, 0.0, 1.0, 1.0

array([0.78052377, 1.39119009])

In [26]:
class_weights

array([0.78052377, 1.39119009])

In [27]:
# max_len = len(Y_train)
max_len = 20000
train_size = int(max_len * 0.80)

train_x = X_train[:train_size]
train_y = Y_train[:train_size]

test_x = X_train[train_size:max_len]
test_y = Y_train[train_size:max_len]

In [28]:
len(train_x), len(train_y), len(test_x), len(test_y)

(16000, 16000, 4000, 4000)

In [29]:

train_x = np.asarray(train_x).astype('float32')#.reshape((-1,1))
train_y = np.asarray(train_y).astype('float32')#.reshape((-1,1))

test_x = np.asarray(test_x).astype('float32')#.reshape((-1,1))
test_y = np.asarray(test_y).astype('float32')#.reshape((-1,1)) 


In [30]:
len(train_x), len(train_y), len(test_x), len(test_y)

(16000, 16000, 4000, 4000)

In [31]:
train_x[0], train_y[0]

(array([  18.,   12.,   83.,   37.,  366.,  615., 1001.,    0.,    0.,
           0.,    0.,    0.,    0.,    0.,    0.,    0.,    0.,    0.,
           0.,    0.,    0.,    0.,    0.,    0.,    0.,    0.,    0.,
           0.,    0.,    0.,    0.,    0.,    0.,    0.,    0.,    0.,
           0.,    0.,    0.,    0.,    0.,    0.,    0.,    0.,    0.,
           0.,    0.,    0.,    0.,    0.], dtype=float32),
 1.0)

In [32]:
X_train

array([[   18,    12,    83, ...,     0,     0,     0],
       [   31,  1845,  4829, ...,     0,     0,     0],
       [ 4698, 10958,    45, ...,     0,     0,     0],
       ...,
       [  133,  1846,  2548, ...,     0,     0,     0],
       [ 1645,   568,    90, ...,     4,     1,  1760],
       [   42,  1538,    11, ...,     0,     0,     0]])

In [34]:
class_weights = {i : class_weights[i] for i in range(2)}
class_weights

{0: 0.7805237651143109, 1: 1.3911900918559514}

In [47]:
model.fit(train_x, train_y,  validation_data=(test_x, test_y), callbacks=callbacks_list, verbose=1, epochs=200, class_weight=class_weights)


Epoch 1/200
500/500 [==============================] - 29s 10ms/step - loss: 0.6124 - acc: 0.6346 - val_loss: 0.5565 - val_acc: 0.7023 - lr: 0.0010
Epoch 2/200
500/500 [==============================] - 5s 10ms/step - loss: 0.4146 - acc: 0.7952 - val_loss: 0.4759 - val_acc: 0.7598 - lr: 0.0010
Epoch 3/200
500/500 [==============================] - 5s 10ms/step - loss: 0.2945 - acc: 0.8610 - val_loss: 0.5901 - val_acc: 0.7312 - lr: 0.0010
Epoch 4/200
500/500 [==============================] - 5s 10ms/step - loss: 0.2082 - acc: 0.9034 - val_loss: 0.6918 - val_acc: 0.7390 - lr: 0.0010
Epoch 5/200
500/500 [==============================] - 5s 10ms/step - loss: 0.1483 - acc: 0.9321 - val_loss: 0.9308 - val_acc: 0.7303 - lr: 0.0010
Epoch 6/200
500/500 [==============================] - 5s 10ms/step - loss: 0.1106 - acc: 0.9486 - val_loss: 1.1531 - val_acc: 0.7442 - lr: 0.0010
Epoch 7/200
500/500 [==============================] - 5s 10ms/step - loss: 0.0935 - acc: 0.9580 - val_loss: 1.3230 -

In [ ]:
model = tuner.get_best_models(num_models=1)[0]

In [56]:
b = model.predict(X_dev0)

for i in b:
    print(round(i[0]))
    
    
with open('dev_out.txt','w+') as f:
    for i in b:
        f.write(str(round(i[0])))
        f.write('\n')
# X_test

0
0
1
0
0
0
0
1
1
1
0
1
0
1
0
1
0
0
1
1
1
0
1
1
1
0
1
1
1
1
0
1
0
0
0
0
1
0
1
0
1
0
0
1
0
0
1
0
0
1
1
0
1
0
1
0
1
0
0
0
0
1
0
1
0
1
1
1
1
0
1
0
1
1
0
1
1
0
1
1
1
1
1
1
0
1
1
1
0
1
0
0
0
0
0
0
0
1
1
0
0
1
0
1
0
1
0
0
0
1
1
0
0
1
0
1
1
0
1
0
1
1
0
0
0
0
0
0
1
0
0
1
0
0
0
1
1
0
1
0
0
0
1
1
1
0
0
1
0
1
1
1
0
1
1
0
1
1
1
1
0
1
0
1
1
1
0
0
0
0
0
1
1
0
1
1
1
1
0
0
0
1
1
0
1
0
0
0
0
0
1
0
0
1
1
0
0
1
1
1
1
0
1
1
0
1
1
0
1
0
0
0
1
0
0
1
0
1
0
1
0
1
0
0
0
0
0
1
0
1
0
0
1
1
1
1
0
0
1
0
0
1
1
1
0
1
0
0
0
0
0
1
1
1
1
0
0
0
0
1
0
1
1
0
1
0
1
0
1
0
1
0
0
0
0
0
1
0
0
1
0
0
1
1
1
0
1
1
0
0
0
0
0
0
0
1
0
0
1
1
1
1
1
1
0
1
1
1
0
1
0
1
0
0
0
1
0
0
0
0
0
1
0
1
1
0
0
0
1
1
0
0
1
0
1
1
0
1
0
0
0
1
0
0
1
1
0
0
0
0
1
0
0
1
0
1
1
0
1
0
0
1
1
1
0
1
0
0
0
1
0
0
0
0
1
0
1
0
1
1
0
0
0
1
0
0
1
0
1
0
0
1
1
0
0
0
0
1
0
0
1
1
0
0
0
0
1
0
0
1
0
0
0
1
1
1
1
1
1
0
0
0
0
0
1
0
0
0
0
0
1
1
1
1
0
0
1
1
1
0
0
0
1
0
0
1
1
0
1
1
1
0
0
0
0
1
1
0
0
1
1
0
1
0
1
1
0
0
1
1
1
0
0
1
1
0
0
0
0
0
1
0
1
1
0
1
0
1
0
1
0
0
1
0
0
0
0
0
0
1


1
1
0
0
1
1
1
1
1
0
0
0
0
1
0
1
1
1
0
0
1
0
1
1
0
1
1
0
0
0
1
0
1
0
0
0
0
0
1
1
1
0
0
0
1
0
0
0
0
1
1
0
1
1
1
0
0
0
1
1
0
0
0
0
1
0
1
0
0
0
0
1
1
1
1
0
1
1
1
0
1
0
0
0
1
1
0
1
1
1
1
0
0
0
1
1
0
0
1
0
0
0
1
1
0
0
0
0
1
0
1
0
1
0
0
0
1
0
0
1
1
1
1
0
1
1
1
1
0
1
1
0
1
0
0
0
1
0
1
0
1
1
0
0
0
1
0
1
1
1
0
0
0
0
0
1
1
1
0
1
1
1
0
1
1
0
0
0
0
0
0
1
0
1
1
1
1
0
0
0
1
0
0
1
1
0
0
0
0
0
1
1
1
1
1
1
0
0
1
0
1
0
0
0
0
0
0
1
0
1
1
1
1
0
1
1
1
0
0
1
0
0
1
1
0
1
0
1
1
0
0
1
1
0
0
0
1
1
0
0
0
0
0
0
1
1
1
0
0
0
0
0
1
1
0
1
0
0
1
1
1
0
0
0
0
1
0
0
1
1
1
1
0
0
0
0
1
0
1
0
1
0
0
1
0
0
1
0
0
1
1
0
0
0
1
0
1
1
1
1
0
1
0
0
1
1
1
1
0
0
0
1
0
0
0
0
0
1
1
0
1
0
0
1
0
0
0
0
0
1
1
1
1
0
0
1
1
0
0
0
0
1
0
1
0
0
0
1
1
1
1
0
1
1
1
1
0
0
1
1
1
0
0
0
1
1
0
0
0
0
1
0
1
1
1
0
0
0
1
1
1
0
1
0
0
0
1
0
0
1
0
1
1
1
1
1
1
1
1
1
0
1
0
0
0
0
0
0
1
1
1
0
1
1
0
0
1
1
1
0
1
1
1
1
0
0
1
1
0
1
0
0
1
0
1
0
0
1
1
1
1
0
0
1
0
0
0
0
1
0
0
1
0
1
0
1
0
0
0
1
1
1
0
0
0
0
1
1
0
0
1
1
1
0
1
0
0
1
1
1
1
1
0
0
0
1
1
0
0
0
1
0
1
1
0
0
0
0
0
1


In [73]:
c = model.predict(X_test)

for i in c:
    print(round(i[0]))
    
    
with open('test_out.txt','w+') as f:
    for i in c:
        f.write(str(round(i[0])))
        f.write('\n')

0
1
1
0
0
0
0
0
1
0
1
0
0
1
0
0
1
1
0
1
1
0
0
1
1
0
1
1
0
0
1
0
1
0
0
0
0
0
1
0
0
1
0
0
0
0
0
1
0
0
0
1
1
0
0
0
1
0
1
0
1
0
0
0
0
0
1
0
1
0
1
0
1
1
0
1
1
1
1
0
0
0
0
1
1
1
0
1
1
0
1
1
1
1
1
0
0
0
1
1
0
0
0
1
0
1
1
1
0
0
1
1
0
1
1
0
0
0
1
0
1
0
0
1
0
0
1
0
1
0
0
0
0
1
0
0
0
0
1
1
1
1
0
1
0
1
0
1
1
0
1
1
0
1
1
1
1
0
0
0
0
0
1
1
0
1
1
0
1
1
0
0
1
1
1
0
1
0
1
0
1
0
0
1
0
0
1
0
1
0
1
0
0
0
1
0
0
0
0
0
1
1
1
1
0
0
0
0
1
0
0
0
0
0
0
0
1
1
0
0
0
1
1
0
0
0
0
0
0
1
0
0
0
1
1
0
0
0
0
0
0
1
1
1
1
0
1
0
1
1
0
1
1
1
1
1
0
0
0
0
0
0
0
1
0
0
0
0
0
0
1
1
0
1
0
1
0
1
1
0
0
1
1
0
1
1
1
1
1
1
0
0
0
0
0
0
0
1
1
1
0
0
0
1
0
0
0
0
0
1
1
0
1
0
0
1
0
1
1
1
0
1
0
0
0
1
1
1
0
0
0
1
0
1
0
0
0
0
1
1
0
0
0
1
1
0
0
0
0
1
1
1
0
1
1
0
1
1
1
1
1
0
0
0
1
0
0
0
1
1
1
0
0
0
0
1
0
0
1
0
1
1
0
0
1
0
1
0
0
0
1
1
0
0
0
0
1
1
0
0
1
1
0
0
0
1
1
0
0
1
1
0
1
0
1
1
0
1
0
1
0
1
0
0
1
1
0
1
1
1
0
0
0
0
1
1
1
1
0
1
0
1
1
1
1
0
1
1
1
1
1
1
0
0
0
1
0
0
1
0
0
0
0
0
0
0
0
0
0
1
1
0
0
0
0
1
1
0
0
1
0
1
1
0
1
0
1
0
1
0
1
0
1
0
1
0
1
1
0
0


0
0
0
0
1
1
0
1
1
0
0
0
1
1
1
1
0
0
0
0
1
1
0
0
1
1
1
0
0
0
0
0
1
1
0
1
1
0
1
0
0
1
0
0
0
0
1
1
1
0
0
1
1
1
0
1
0
0
0
1
1
1
0
1
0
1
1
0
1
1
0
1
1
0
1
1
0
1
0
0
0
0
1
1
1
0
1
0
0
1
1
1
1
1
1
0
0
1
1
1
0
0
1
1
1
1
0
1
1
0
1
0
1
0
0
1
0
1
0
1
0
1
1
0
1
0
1
1
0
1
0
1
0
0
0
1
1
0
1
1
0
1
0
0
0
1
0
0
0
1
0
1
1
1
0
1
0
0
0
0
1
0
0
1
1
0
0
0
1
1
1
1
1
0
1
0
1
0
1
0
1
0
0
1
1
0
0
0
0
0
0
1
1
1
1
0
0
1
0
0
1
1
0
0
1
0
1
0
0
1
1
1
0
0
0
1
0
0
0
0
0
1
1
0
0
0
1
1
1
0
0
1
0
0
0
0
0
0
1
0
0
1
1
0
0
1
1
0
1
0
0
1
0
1
1
1
0
1
1
0
0
1
1
1
1
1
1
0
1
0
1
0
1
0
0
0
0
1
1
1
1
1
1
1
0
1
0
0
0
0
1
0
0
0
0
0
1
0
1
0
1
0
1
1
0
0
0
0
0
1
0
1
0
0
1
0
0
1
1
1
1
1
1
1
0
0
0
0
0
1
1
1
0
0
1
0
0
0
1
1
1
1
1
1
0
0
1
0
0
1
1
0
0
0
0
1
1
0
1
0
1
1
0
1
0
0
1
0
1
1
0
1
0
1
1
1
1
1
0
0
1
1
0
1
0
1
0
0
0
1
0
1
0
1
1
0
0
0
0
1
0
0
0
0
0
1
1
1
1
0
0
0
0
1
0
0
0
0
0
0
0
1
0
1
0
1
0
0
0
1
0
0
0
1


In [61]:
y_expected_dev0 = [float(i.replace('\n', '')) for i in y_expected_dev0]
y_expected_dev0 = [int(i) for i in y_expected_dev0]
y_expected_dev0

[0,
 1,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 1,
 0,
 1,
 0,
 1,
 1,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 1,
 1,
 0,
 1,
 0,
 1,
 1,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 1,
 0,
 1,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 1,
 1,
 0,
 0,
 1,
 1,
 0,
 1,
 1,
 0,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 1,
 0,
 0,
 1,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 1,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 0,
 1,
 1,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 1,
 1,
 1,
 0,
 0,
 0,
 1,
 1,
 1,
 1,
 0,
 0,
 1,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 1,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 1,
 1,
 1,
 0,
 0,


In [63]:
temp_b = [int(round(i[0])) for i in b]
temp_b

[0,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 1,
 1,
 0,
 1,
 0,
 1,
 0,
 1,
 0,
 0,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 1,
 0,
 0,
 1,
 0,
 0,
 1,
 0,
 0,
 1,
 1,
 0,
 1,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 1,
 1,
 1,
 1,
 0,
 1,
 0,
 1,
 1,
 0,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 0,
 1,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 1,
 1,
 0,
 0,
 1,
 0,
 1,
 1,
 0,
 1,
 0,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 0,
 1,
 1,
 1,
 0,
 0,
 1,
 0,
 1,
 1,
 1,
 0,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 0,
 1,
 0,
 1,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 0,
 0,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 1,
 1,
 0,
 0,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 1,
 0,
 1,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 1,
 1,
 1,
 1,
 0,
 0,
 1,
 0,
 0,
 1,
 1,
 1,
 0,
 1,
 0,
 0,
 0,
 0,


In [65]:
from sklearn.metrics import accuracy_score
accuracy_score(y_expected_dev0, temp_b)

0.7310318664643399

In [68]:
X_test

['Gentleman, I believe we can agree that this is a victory.\t1304170330\n',
 'The problem is that it will just turn it r/nosleep. But yeah, go for gold. \t1353763204\n',
 "Well, according to some Christian apologists, the fact that places described in the bible exist prove its reliability. So obviously, Hercules is real, too. I'm hoping by extension this means Xena is real.\t1336314173\n",
 "Don't know if this is what you are looking for, but The Skeptics Guide to the Universe podcast had an episode about a month or so  ago where they talked about the scientific\\\\logic flaws in this movie for a good 15-20 minutes.\t1348860314\n",
 "I respect what you're saying completely. I just don't think and process things the same way. \t1341285952\n",
 "You're asking this of the History Channel when Fox News is still widely available and watched?\t1323714877\n",
 "I don't know that it's parachuters, but it's much better than your blimp theory.  You were the one coming across as the douchey exper